In [ ]:
!pip install --upgrade pip
!pip install -q textgenrnn

In [9]:
!pip3 install --upgrade scipy
!pip install --upgrade six
!pip install --upgrade grpcio

Requirement already up-to-date: scipy in /home/ec2-user/anaconda3/envs/amazonei_tensorflow_p36/lib/python3.6/site-packages (1.4.1)
ERROR: tensorflow-serving-api 1.14.0 has requirement tensorflow~=1.14.0, but you'll have tensorflow 2.1.0 which is incompatible.
ERROR: tensorboard 2.1.0 has requirement grpcio>=1.24.3, but you'll have grpcio 1.16.0 which is incompatible.
  Attempting uninstall: six
    Found existing installation: six 1.11.0
    Uninstalling six-1.11.0:
      Successfully uninstalled six-1.11.0
     |████████████████████████████████| 2.7 MB 3.2 MB/s eta 0:00:01
ERROR: tensorflow-serving-api 1.14.0 has requirement tensorflow~=1.14.0, but you'll have tensorflow 2.1.0 which is incompatible.
  Attempting uninstall: grpcio
    Found existing installation: grpcio 1.16.0
    Uninstalling grpcio-1.16.0:
      Successfully uninstalled grpcio-1.16.0


In [20]:
import pandas as pd
import numpy as np
import unicodedata
import string
import re
import matplotlib.pyplot as plt

from nltk.tokenize import word_tokenize
from nltk.tokenize import sent_tokenize
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
from nltk.stem.snowball import SnowballStemmer
from nltk.util import ngrams

from textgenrnn import textgenrnn

from tensorflow import keras
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout, Activation
from tensorflow.keras.layers import LSTM

In [123]:
df = pd.read_csv('./drinksandcocktails_1.0.9.csv', escapechar='\\')

In [124]:
df.columns

Index(['id', 'd_name', 'd_cat', 'd_alcohol', 'd_glass', 'd_ingredients',
       'd_instructions', 'd_shopping'],
      dtype='object')

In [125]:
df

id                                  d_name                 d_cat  \
0          1                        110 in the shade                  Beer   
1          2                               '57 Chevy              Cocktail   
2          3                          1-900-FUK-MEUP                  Shot   
3          4                            '57 Chevy #2                  Shot   
4          5                                187 URge              Cocktail   
5          6                   The "Liquerice" Dream                  Shot   
6          7    '57 Chevy with a White License Plate              Cocktail   
7          8                                 220 BTU                  Shot   
8          9                              3 Wise Men                  Shot   
9         10                  151 Florida Bushwacker  Milk / Float / Shake   
10        11                             155 Belmont              Cocktail   
11        12                                     252                  Shot   
12        13             3-Mile Long Island Iced Tea        Ordinary Drink   
13        14                           24k nightmare                  Shot   
14        15                             351 Special        Ordinary Drink   
15        16                              357 Magnum        Ordinary Drink   
16        17                                    3001        Ordinary Drink   
17        18                               3rd Wheel              Cocktail   
18        19                    3rd Street Promanade              Cocktail   
19        20                             360 degress              Cocktail   
20        21                                    5 Pm          Coffee / Tea   
21        22                                     44D                  Shot   
22        23                                   50/50        Ordinary Drink   
23        24                                40 Water        Ordinary Drink   
24        25                                     491        Ordinary Drink   
25        26                                  5-Ball   Punch / Party Drink   
26        27                                501 Blue        Ordinary Drink   
27        28                          49er Gold Rush                  Shot   
28        29                                     666                  Shot   
29        30  57 T-Bird with Hawaiian License Plates              Cocktail   
...      ...                                     ...                   ...   
16321  16322                            Yang Martini              Cocktail   
16322  16323                       Yarmouth Cadillac              Cocktail   
16323  16324                          Yellow Bird #2              Cocktail   
16324  16325                            Yellow Fever              Cocktail   
16325  16326                          Yellow Fingers              Cocktail   
16326  16327                            Yellow Peril              Cocktail   
16327  16328                        Yeoman's Passion              Cocktail   
16328  16329                                    Yes!              Cocktail   
16329  16330                             Yin Martini              Cocktail   
16330  16331                              Yule Toddy              Cocktail   
16331  16332                            Yellow Boxer              Cocktail   
16332  16333                                 Yum-Yum              Cocktail   
16333  16334                             Zack Attack              Cocktail   
16334  16335                                   Za Za              Cocktail   
16335  16336                            Zach's Mambo              Cocktail   
16336  16337                            Zero Gravity              Cocktail   
16337  16338                            Zen Saketini              Cocktail   
16338  16339                           Zen Sake-tini              Cocktail   
16339  16340                               Zerg Rush              Cocktail   
16340  16341                    

In [152]:
df_drink = df[(df['d_cat'] == 'Ordinary Drink') | (df['d_cat'] == 'Cocktail')]

In [153]:
df_drink

id                                  d_name           d_cat  \
1          2                               '57 Chevy        Cocktail   
4          5                                187 URge        Cocktail   
6          7    '57 Chevy with a White License Plate        Cocktail   
10        11                             155 Belmont        Cocktail   
12        13             3-Mile Long Island Iced Tea  Ordinary Drink   
14        15                             351 Special  Ordinary Drink   
15        16                              357 Magnum  Ordinary Drink   
16        17                                    3001  Ordinary Drink   
17        18                               3rd Wheel        Cocktail   
18        19                    3rd Street Promanade        Cocktail   
19        20                             360 degress        Cocktail   
22        23                                   50/50  Ordinary Drink   
23        24                                40 Water  Ordinary Drink   
24        25                                     491  Ordinary Drink   
26        27                                501 Blue  Ordinary Drink   
29        30  57 T-Bird with Hawaiian License Plates        Cocktail   
31        32                              69 Special  Ordinary Drink   
32        33                         The 5th Element        Cocktail   
37        38                             9 1/2 Weeks        Cocktail   
38        39                               78 Camaro        Cocktail   
39        40                         77 Sunset Strip  Ordinary Drink   
40        41                               81 Camaro        Cocktail   
43        44                                   A 243  Ordinary Drink   
44        45                      A Day at the Beach  Ordinary Drink   
45        46                           A Fuzzy Thing        Cocktail   
46        47                      A Better Melonball  Ordinary Drink   
47        48                        A Goodnight Kiss        Cocktail   
48        49                             915 Special        Cocktail   
49        50                     A Gilligan's Island        Cocktail   
50        51                      A Furlong Too Late  Ordinary Drink   
...      ...                                     ...             ...   
16321  16322                            Yang Martini        Cocktail   
16322  16323                       Yarmouth Cadillac        Cocktail   
16323  16324                          Yellow Bird #2        Cocktail   
16324  16325                            Yellow Fever        Cocktail   
16325  16326                          Yellow Fingers        Cocktail   
16326  16327                            Yellow Peril        Cocktail   
16327  16328                        Yeoman's Passion        Cocktail   
16328  16329                                    Yes!        Cocktail   
16329  16330                             Yin Martini        Cocktail   
16330  16331                              Yule Toddy        Cocktail   
16331  16332                            Yellow Boxer        Cocktail   
16332  16333                                 Yum-Yum        Cocktail   
16333  16334                             Zack Attack        Cocktail   
16334  16335                                   Za Za        Cocktail   
16335  16336                            Zach's Mambo        Cocktail   
16336  16337                            Zero Gravity        Cocktail   
16337  16338                            Zen Saketini        Cocktail   
16338  16339                           Zen Sake-tini        Cocktail   
16339  16340                               Zerg Rush        Cocktail   
16340  16341                                    Zico        Cocktail   
16341  16342                               Zip Drive        Cocktail   
16342  16343                                  Zombie        Cocktail   
16343  16344                                  Zocolo        Cocktail   
16344  16345                                 Zolez

In [154]:
df_drink.isnull().sum()

id                0
d_name            0
d_cat             0
d_alcohol         0
d_glass           0
d_ingredients     0
d_instructions    7
d_shopping        0
dtype: int64

In [155]:
df_drink = df_drink.dropna(axis='index')

In [156]:
df_drink['ingredients'] = (df_drink['d_ingredients'].str.split('|').str.join(', ').tolist())

/home/ec2-user/anaconda3/envs/amazonei_tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


In [159]:
df_drink

id                                  d_name           d_cat  \
1          2                               '57 Chevy        Cocktail   
4          5                                187 URge        Cocktail   
6          7    '57 Chevy with a White License Plate        Cocktail   
10        11                             155 Belmont        Cocktail   
12        13             3-Mile Long Island Iced Tea  Ordinary Drink   
14        15                             351 Special  Ordinary Drink   
15        16                              357 Magnum  Ordinary Drink   
16        17                                    3001  Ordinary Drink   
17        18                               3rd Wheel        Cocktail   
18        19                    3rd Street Promanade        Cocktail   
19        20                             360 degress        Cocktail   
22        23                                   50/50  Ordinary Drink   
23        24                                40 Water  Ordinary Drink   
24        25                                     491  Ordinary Drink   
26        27                                501 Blue  Ordinary Drink   
29        30  57 T-Bird with Hawaiian License Plates        Cocktail   
31        32                              69 Special  Ordinary Drink   
32        33                         The 5th Element        Cocktail   
37        38                             9 1/2 Weeks        Cocktail   
38        39                               78 Camaro        Cocktail   
39        40                         77 Sunset Strip  Ordinary Drink   
40        41                               81 Camaro        Cocktail   
43        44                                   A 243  Ordinary Drink   
44        45                      A Day at the Beach  Ordinary Drink   
45        46                           A Fuzzy Thing        Cocktail   
46        47                      A Better Melonball  Ordinary Drink   
47        48                        A Goodnight Kiss        Cocktail   
48        49                             915 Special        Cocktail   
49        50                     A Gilligan's Island        Cocktail   
50        51                      A Furlong Too Late  Ordinary Drink   
...      ...                                     ...             ...   
16321  16322                            Yang Martini        Cocktail   
16322  16323                       Yarmouth Cadillac        Cocktail   
16323  16324                          Yellow Bird #2        Cocktail   
16324  16325                            Yellow Fever        Cocktail   
16325  16326                          Yellow Fingers        Cocktail   
16326  16327                            Yellow Peril        Cocktail   
16327  16328                        Yeoman's Passion        Cocktail   
16328  16329                                    Yes!        Cocktail   
16329  16330                             Yin Martini        Cocktail   
16330  16331                              Yule Toddy        Cocktail   
16331  16332                            Yellow Boxer        Cocktail   
16332  16333                                 Yum-Yum        Cocktail   
16333  16334                             Zack Attack        Cocktail   
16334  16335                                   Za Za        Cocktail   
16335  16336                            Zach's Mambo        Cocktail   
16336  16337                            Zero Gravity        Cocktail   
16337  16338                            Zen Saketini        Cocktail   
16338  16339                           Zen Sake-tini        Cocktail   
16339  16340                               Zerg Rush        Cocktail   
16340  16341                                    Zico        Cocktail   
16341  16342                               Zip Drive        Cocktail   
16342  16343                                  Zombie        Cocktail   
16343  16344                                  Zocolo        Cocktail   
16344  16345                                 Zolez

In [160]:
df_drink[df_drink['ingredients'].str.contains("1/88")]

id                     d_name           d_cat  d_alcohol  \
18        19       3rd Street Promanade        Cocktail  Alcoholic   
188      189              Almond Cooler  Ordinary Drink  Alcoholic   
627      628           Black Martini #1  Ordinary Drink  Alcoholic   
674      675              Blonde Moment        Cocktail  Alcoholic   
1744    1745         Down Home Punch #2        Cocktail  Alcoholic   
2288    2289    Genuine Singapore Sling  Ordinary Drink  Alcoholic   
2902    2903  J's Tropical Orgasm (JTO)        Cocktail  Alcoholic   
3108    3109                   Kameleon        Cocktail  Alcoholic   
3204    3205                      Kosmo        Cocktail  Alcoholic   
3574    3575     Martini (Dry) (5-to-1)        Cocktail  Alcoholic   
3674    3675              Midori Mimosa        Cocktail  Alcoholic   
4501    4502      Quarter Deck Cocktail  Ordinary Drink  Alcoholic   
4777    4778                  Rum Snapp        Cocktail  Alcoholic   
5004    5005        Sex on the Beach #4        Cocktail  Alcoholic   
5457    5458                StumbleFuck  Ordinary Drink  Alcoholic   
5854    5855                    The Two  Ordinary Drink  Alcoholic   
5888    5889              The Valentine        Cocktail  Alcoholic   
8168    8169            Amaretto Colada        Cocktail  Alcoholic   
8198    8199                    Amnesia        Cocktail  Alcoholic   
8233    8234                   Anjorska        Cocktail  Alcoholic   
8238    8239           Annabele Special        Cocktail  Alcoholic   
8256    8257      Ann Sheridan Cocktail        Cocktail  Alcoholic   
8260    8261                   Apollo 1        Cocktail  Alcoholic   
8366    8367            Arch de Triumph        Cocktail  Alcoholic   
8368    8369                 Arctic Red        Cocktail  Alcoholic   
8372    8373          Arcturian Sunrise        Cocktail  Alcoholic   
8405    8406                   Assassin        Cocktail  Alcoholic   
8453    8454                       B-28        Cocktail  Alcoholic   
8557    8558                    Ballack        Cocktail  Alcoholic   
8582    8583             Banana Hammock        Cocktail  Alcoholic   
...      ...                        ...             ...        ...   
15424  15425                 Rum Ramsay        Cocktail  Alcoholic   
15427  15428                 Rum Scaffa        Cocktail  Alcoholic   
15428  15429              Rum Scoundrel        Cocktail  Alcoholic   
15430  15431                   Rum Snap        Cocktail  Alcoholic   
15502  15503               Saronno Rose        Cocktail  Alcoholic   
15585  15586             Sherry Cobbler        Cocktail  Alcoholic   
15646  15647         Slow Gin and Tonic        Cocktail  Alcoholic   
15662  15663                     Slaber        Cocktail  Alcoholic   
15666  15667              Smooth Sailor        Cocktail  Alcoholic   
15689  15690                Sore Throat        Cocktail  Alcoholic   
15707  15708             Southern Delta        Cocktail  Alcoholic   
15782  15783          Strawberry Colada        Cocktail  Alcoholic   
15802  15803                Strike's On        Cocktail  Alcoholic   
15843  15844            Surprise Browst        Cocktail  Alcoholic   
15847  15848               Swedish Blue        Cocktail  Alcoholic   
15853  15854          Sweet Cherry Sour        Cocktail  Alcoholic   
15854  15855    Sweet and Sour Rockstar        Cocktail  Alcoholic   
15867  15868               Sydney Sling        Cocktail  Alcoholic   
15966  15967                  The Fiona        Cocktail  Alcoholic   
15992  15993                   The Ogie        Cocktail  Alcoholic   
16063  16064        Tonight's the Night        Cocktail  Alcoholic   
16069  16070               Touch of Zam        Cocktail  Alcoholic   
16098  16099         Tropical Orgasm #3        Cocktail  Alcoholic   
16109  16110                Tropicolada        Cocktail  Alcoholic   
16185  16186            Viking's Helmet        Cocktail  Alcoholic   
16205  16206        

In [134]:
df_drink.loc[9412, 'ingredients'] = '3785 mllon Everclear(R) alcohol, 1 1892 mllons vodka, 7570 mls orange juice'

'3785 mllon Everclear(R) alcohol, 1 1892 mllons vodka, 7570 mls orange juice'

In [151]:
df_drink.loc[9412, 'ingredients'] 

'3785 ml Everclear(R) alcohol, 1 1892 mls vodka, 7570 ml orange juice'

In [50]:
f = lambda x: 'ingredient_{}'.format(x + 1)
ingred = pd.DataFrame(df_drink.ingredients.values.tolist(), df_drink.index).fillna('').rename(columns=f)

In [51]:
ingred

ingredient_1
1      1/2 oz Vodka, 1 1/2 oz Southern Comfort, 1/2 o...
4      44 ml Jack Daniels, 44 ml Vodka, 266 ml Dr. Pe...
6                  1 oz white Creme de Cacao, 1 oz Vodka
10     44 ml Dark rum, 88 ml Light rum, 44 ml Vodka, ...
12     1/2 oz Gin, 1/2 oz Light rum, 1/2 oz Tequila, ...
14     1 part Coca-Cola, 1 part Gin (Gordon's), 2 spl...
15     1 oz Vodka (Smirnoff), 1 oz Rum (Captain Morga...
16     1 oz Blue Curacao, 1 oz Vodka, 1/2 oz Tonic wa...
17                   2 parts Alize, 1 part Grand Marnier
18     1 1/2 oz Vanilla vodka (Stoli), 1/3 oz Gin, 1/...
19     1/2 oz Rum, 1/2 oz Grape juice, 1/2 oz Vodka, ...
22     2 1/2 oz Vanilla vodka (Stoli Vanil), 1 splash...
23     1 1/2 oz Bacardi 151 proof rum, 1 1/2 oz Light...
24     2 cl White rum (Bacardi), 2 cl Gin (Tanqueray)...
26     Blue Curacao, Blueberry schnapps, Vodka, Sour ...
29     1 oz Vodka, 1 oz Amaretto, 1 oz Grand Marnier,...
31     2 oz dry Gin (Gordon's), 4 oz 7-Up, 0.75 oz Le...
32     3 oz Pineapple juice, 3 oz Sprite, 1 oz Bacard...
37     2 oz Absolut Citron, 1/2 oz Orange Curacao, 1 ...
38     3/4 oz Yukon Jack, 3/4 oz Rum (Captian Morgan'...
39     1/2 oz Vodka (Finlandia), 1/2 oz Gin (Tanquera...
40     4 oz Vanilla ice-cream, 4 oz Vodka (Popov), 2 ...
43     2 cl Vodka (Absolut), 2 cl Licor 43, 2 cl Blue...
44     1 oz Coconut rum, 1/2 oz Amaretto, 4 oz Orange...
45     2 oz Absolut Citron, 1 oz Triple sec, 1 1/2 oz...
46     1 oz Midori melon liqueur, 1/2 oz Peachtree sc...
47     4 oz Champagne, 1 splash Campari, 1 cube Sugar...
48     1/2 jigger Light rum, 1/2 jigger Dark rum, 8 o...
49     1 oz Vodka, 1 oz Peach schnapps, 3 oz Orange j...
50     2 oz Light rum, 4 oz Ginger beer, 1 twist of L...
...                                                  ...
16321                    3 oz gin, 1/2 oz sake rice wine
16322  2 oz Captain Morgan(R) spiced rum, 1 oz Gibson...
16323  1 oz dark rum, 1 oz white rum, 1/4 oz Galliano...
16324  1 1/2 oz vodka, 1/4 oz Galliano(R) herbal liqu...
16325  1 oz Southern Comfort(R) peach liqueur, 1 oz v...
16326  1 oz Finlandia(R) lime vodka, 1 oz Galliano(R)...
16327  1 oz Beefeater(R) gin, 1 oz Pisang Ambon(R) li...
16328  1 oz Malibu(R) coconut rum, 1 oz Passoa(R) liq...
16329                    3 oz sake rice wine, 1/2 oz gin
16330  2 oz ginger brandy, 1 oz Barenjager(R) honey l...
16331  1 3/4 oz tequila, 1/4 oz Galliano(R) herbal li...
16332  1 1/2 oz white rum, 1/2 oz coconut rum, 1 oz m...
16333  8 oz Faygo(R) Classic blueberry soda, 2 oz Smi...
16334  1 1/2 oz gin, 1 1/2 oz Dubonnet(R) Rouge vermo...
16335  2 oz Hpnotiq(R) liqueur, 0.5 oz Malibu(R) coco...
16336  1 can Vault(R) Zero, 3 oz triple sec, 2 oz Mal...
16337  1 oz Zen(R) green tea liqueur, 2 ozdry sake ri...
16338  2 ozOzeki traditional sake rice wine, 1 oz Zen...
16339  2 oz gin, 5 ozBAWLS GuaranaA(R) energy soda, 1...
16340  1 oz Sagatiba Pura, 1 oz white rum, 2 oz papay...
16341  3/4 oz Gosling's(R) black rum, 1/2 oz brandy, ...
16342  1/2 oz Bacardi(R) 151 rum, 1 oz pineapple juic...
16343  1 oz dark rum, 1/2 oz tequila, 2 oz pineapple ...
16344  44 ml Midori(R) melon liqueur, 44 ml Blue Cura...
16345  4 cl lemon juice, 1 dash grenadine syrup, 2 cl...
16346  1/2 oz light rum, 3/4 oz gold rum, 1/4 oz apri...
16347  1 oz creme de cassis, 1 oz vodka, 1/2 oz peach...
16348  1 oz creme de cacao, 1 oz amaretto almond liqu...
16349  2 oz tequila, 1/2 oz Galliano(R) herbal liqueu...
16350  1 oz dark rum, 1 oz dark creme de cacao, 1/2 o...

[12294 rows x 1 columns]

In [48]:
# df_drink = df_drink.replace(regex={('1 shot'): '44 ml', ('1 1/2 shot'): '66 ml', ('1 1/2 shot'): '66 ml',
#                                        ('^2 shot'): '88 ml', '3 shot': '133 ml', '1/2 shot': '22 ml',
#                                       '1 - 2 shot': '44-88 ml', '3/4 shot': ', 33 ml', '1.5 shots': '66 ml', 
#                                       '1.5 shots': '66 ml', '2 shots': '88 ml', '4 shots': '177 ml',
#                                       '6 shots': '266 ml', '5 shots': '222 ml', '1/2 shot': '22 ml',
#                                       '1/4 shot': '11 ml', '1/4 shot': '11 ml', '1-2 shot': '44-88 ml',
#                                       '1-2 shot': '44-88 ml', '12 shots': '532 ml', '4 shots': '177 ml',
#                                        '5 shots': '222 ml', '3/4 shot': '33 ml', '1 1/2 - 2': '66-88 ml',
#                                       '8 shots': '355 ml', '1 or 2 shot': '44-88 ml', '1 or 2 shot': '44-88 ml',
#                                        '1.5 shot': '66 ml', '30 shots': '1330 ml', '0.5 shot': '22 ml',
#                                   '2 shot': '88 ml'})

df_drink = df_drink.replace(regex={('1 shot'): '44 ml', ('1 1/2 shot'): '66 ml', (', 1 1/2 shot'): '66 ml',
                                       '2 shot': '88 ml', '3 shot': '133 ml', ', 1/2 shot': ', 22 ml',
                                      '1 - 2 shot': '44-88 ml', ', 3/4 shot': ', 33 ml', '1.5 shots': '66 ml', 
                                      ', 1.5 shots': ', 66 ml', ', 2 shots': ', 88 ml', ', 4 shots': ', 177 ml',
                                      ', 6 shots': ', 266 ml', ', 5 shots': ', 222 ml', '1/2 shot': '22 ml',
                                      '1/4 shot': '11 ml', ', 1/4 shot': ', 11 ml', ', 1-2 shot': ', 44-88 ml',
                                      '1-2 shot': '44-88 ml', '12 shots': ', 532 ml', '4 shots': '177 ml',
                                       '5 shots': '222 ml', '3/4 shot': '33 ml', ', 1 1/2 - 2': ', 66-88 ml',
                                      ', 8 shots': ', 355 ml', ', 1 or 2 shot': ', 44-88 ml', '1 or 2 shot': '44-88 ml',
                                       ', 1.5 shot': ', 66 ml', ', 30 shots': ', 1330 ml', ', 0.5 shot': ', 22 ml',
                                  ''})

In [ ]:
a[.25, .5, .75, 1, 1.25, 1.5, 1.75, 2, 2.25, 2.5, 2.75, 3]

In [158]:


df_drink = df_drink.replace(regex={('1 shot'): '44 ml', ('1 1/2 shot'): '66 ml', (', 1 1/2 shot'): '66 ml',
                                       ('^2 shot'): '88 ml', '3 shot': '133 ml', ', 1/2 shot': ', 22 ml',
                                      '1 - 2 shot': '44-88 ml', ', 3/4 shot': ', 33 ml', '1.5 shots': '66 ml', 
                                      ', 1.5 shots': ', 66 ml', ', 2 shots': ', 88 ml', ', 4 shots': ', 177 ml',
                                      ', 6 shots': ', 266 ml', ', 5 shots': ', 222 ml', '1/2 shot': '22 ml',
                                      '1/4 shot': '11 ml', ', 1/4 shot': ', 11 ml', ', 1-2 shot': ', 44-88 ml',
                                      '1-2 shot': '44-88 ml', '12 shots': ', 532 ml', '4 shots': '177 ml',
                                       '5 shots': '222 ml', '3/4 shot': '33 ml', ', 1 1/2 - 2 shot': ', 66-88 ml',
                                      ', 8 shots': ', 355 ml', ', 1 or 2 shot': ', 44-88 ml', '1 or 2 shot': '44-88 ml',
                                       ', 1.5 shot': ', 66 ml', ', 30 shots': ', 1330 ml', ', 0.5 shot': ', 22 ml',
                                  ', 2 shot': ', 88 ml', ('1 oz'): '30 ml', ('1.0 oz'): '30 ml', '1 1/2 oz': '44 ml', (', 1 1/2 oz'): '44 ml',
                                       '1/2 oz': '15 ml', '2 oz': '60 ml', '3 oz': '88 ml', ', 1/2 oz': ', 15 ml',
                                      '1 - 2 oz': '30-60 ml', ', 3/4 oz': ', 22 ml', '1.5 oz': '44 ml', 
                                      ', 1.5 oz': ', 44 ml', ', 2 oz': ', 60 ml', ', 4 oz': ', 118 ml',
                                      ', 6 oz': ', 177 ml','6 oz': '177 ml', ', 5 oz': ', 148 ml',
                                      '1/4 oz': '7 ml', ', 1/4 oz': ', 7 ml', ', 1-2 oz': ', 30-60 ml',
                                      '1-2 oz': '30-60 ml', '12 oz': ', 354 ml', '4 oz': '118 ml',
                                       '5 oz': '148 ml', '3/4 oz': '22 ml', ', 1 1/2 - 2 oz': ', 44-60 ml',
                                      ', 8 oz': ', 236 ml', ', 1 or 2 oz': ', 30-60 ml', '1 or 2 oz': '30-60 ml',
                                       ', 1.5 oz': ', 44 ml', ', 30 oz': ', 887 ml', ', 0.5 oz': ', 15 ml',
                                  ', 3 oz': ', 88 ml','7 oz': '207 ml',', 7 oz': ', 207 ml','8 oz': '236 ml',
                                      ', 8 oz': ', 236 ml','9 oz': '266 ml',', 9 oz': ', 266 ml', '2.5 oz':
                                      '74 ml', ', 2.5 oz': ', 74 ml', ', 0.8 oz': ', 23 ml', '10 oz': '296 ml', 
                                      ', 10 oz': ', 296 ml', ', 4-6 oz': ', 118-177 ml', '4-6 oz': '118-177 ml',
                                      '6 - 7 oz': '177-207 ml', '20 oz': '591 ml', ', 20 oz': ', 591 ml', ', 5 - 6 oz':
                                      '147-177 ml', '2.5-3 oz': '74-88 ml', ', 16 oz': ', 473 ml', ', 40 oz': ', 1183 ml',
                                      ', 2 1/2 oz': ', 74 ml', ', 1 liter': ', 1000 ml', '1 gallon': '3785 ml', ', 1 gallon': ', 3785 ml',
                                      ', 1 1/2 gallons': ', 5678 ml', '1/2 gallon': '1892 ml', ', 1/2 gallon': ', 1892 ml', '2 liter': '2000 ml',
                                   ', 2 liter': ', 2000 ml', '1 qt': '946 ml', ', 1 qt': ', 946 ml', '1.5 liter': '1500 ml', ', 1.5 liter': ', 1500 ml',
                                      '2.25 liter': '2250 ml', ', 2.25 liter': ', 2250 ml', '1 cup': '240 ml', ', 1 cup': ', 240 ml',
                                      '2 cup': '480 ml', ', 2 cup': ', 480 ml', '3 liter': '3000 ml', ', 3 liter': ', 3000 ml',
                                      '1/8 liter': '125 ml', ', 1/8 liter': ', 125 ml', '1 pint': '473 ml', ', 1 pint': ', 473 ml',
                                      '2 pint': '946 ml', ', 2 pint': ', 946ml', '1.75 liter': '1750 ml', ', 1.75 liter': ', 1750ml',
                                      '1 liter': '1000 ml', ', 1 liter': ', 1000 ml', ', 2 gallons': ', 7570 ml',
                                       '2 gallons': '7570 ml'})

# df_drinktest = df_drink.replace(regex={('1 oz'): '30 ml', ('1.0 oz'): '30 ml', ('1 1/2 oz'): '44 ml', (', 1 1/2 oz'): '44 ml',
#                                        ('2 oz'): '60 ml', '3 oz': '88 ml', ', 1/2 oz': ', 15 ml',
#                                       '1 - 2 oz': '30-60 ml', ', 3/4 oz': ', 22 ml', '1.5 oz': '44 ml', 
#                                       ', 1.5 oz': ', 44 ml', ', 2 oz': ', 60 ml', ', 4 oz': ', 118 ml',
#                                       ', 6 oz': ', 177 ml','6 oz': '177 ml', ', 5 oz': ', 148 ml', '1/2 oz': '15 ml',
#                                       '1/4 oz': '7 ml', ', 1/4 oz': ', 7 ml', ', 1-2 oz': ', 30-60 ml',
#                                       '1-2 oz': '30-60 ml', '12 oz': ', 354 ml', '4 oz': '118 ml',
#                                        '5 oz': '148 ml', '3/4 oz': '22 ml', ', 1 1/2 - 2 oz': ', 44-60 ml',
#                                       ', 8 oz': ', 236 ml', ', 1 or 2 oz': ', 30-60 ml', '1 or 2 oz': '30-60 ml',
#                                        ', 1.5 oz': ', 44 ml', ', 30 oz': ', 887 ml', ', 0.5 oz': ', 15 ml',
#                                   ', 3 oz': ', 88 ml','7 oz': '207 ml',', 7 oz': ', 207 ml','8 oz': '236 ml',
#                                       ', 8 oz': ', 236 ml','9 oz': '266 ml',', 9 oz': ', 266 ml', '2.5 oz':
#                                       '74 ml', ', 2.5 oz': ', 74 ml', ', 0.8 oz': ', 23 ml', '10 oz': '296 ml', 
#                                       ', 10 oz': ', 296 ml', ', 4-6 oz': ', 118-177 ml', '4-6 oz': '118-177 ml',
#                                       '6 - 7 oz': '177-207 ml', '20 oz': '591 ml', ', 20 oz': ', 591 ml', ', 5 - 6 oz':
#                                       '147-177 ml', '2.5-3 oz': '74-88 ml', ', 16 oz': ', 473 ml'})


In [ ]:
genre_df = pd.DataFrame(merged_movies['Genres'].str.split('|').tolist(), index = merged_movies['MovieID']).stack()
genre_df = genre_df.reset_index([0, 'MovieID'])
genre_df.columns = ['MovieID', 'Genres']

In [40]:
# for i in df_drink['d_ingredients']

df_drink['ingredients'] = pd.DataFrame(df_drink['d_ingredients'].str.split('|').str.join(', ').tolist())
# genre_df = genre_df.reset_index([0, 'id'])


/Users/birdshaw/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [41]:
df_drink.loc[4, 'ingredients']

['44 ml Jack Daniels',
 '44 ml Vodka',
 '6 shots Dr. Pepper',
 '1 dash Sugar',
 '1 piece Cherry']

In [74]:
import json
from textgenrnn import textgenrnn

recipes_file = open('Data/recipes.json')

lines = recipes_file.readlines()

lines = [dict(json.loads(line)) for line in lines]


recipes = []
for line in lines:
    features = []

    description = line['Description']
    ingredients = line['Ingredients']
    method = line['Method']

    for key in [description, ingredients, method]:
        if key != None and len(key) > 0:
            features.append(method)
        recipes.append(features)

recipes_text = [ '.'.join(recipe_list[0]) for recipe_list in recipes]

write_to = open('recipes_text.txt', 'w')
write_to.write('\n'.join(recipes_text))

textgen = textgenrnn()
textgen.train_from_file('recipes_text.txt', num_epochs=20)


for i in range(5):
    textgen.generate()

4,850 texts collected.
Training on 4,782,450 character sequences.
  ...
    to  
  ['...']
Train for 37362 steps
Epoch 1/20
 1622/37362 [>.............................] - ETA: 1:30:05 - loss: 1.2534####################
Temperature: 0.2
####################
Heat oven to 180C/200C fan/gas 7. Pour in a pan of the bowl of the parchment on top of the pan..Pour the boil and stirring the cake and set aside..Pour the top of the pan and parchmently well to cool for 10 mins until the pan is golden and stir in the chocolate and cook for 1 months, then pastry wi

Heat oven to 180C/200C fan/gas 7. Cook the boil and set aside for 1 hours, then pastry to cook the pancake and put the cake and set aside for 1 mins until some set and pastry and serve with the baking parchment, then top and stirring the baking parchment, then top off the parchment and completely w

Heat oven to 180C/200C fan/gas 7. Cook the straight parchments, then cook the tin and stirring the pastry and cook for 1 mins until the top o

KeyboardInterrupt: 

In [73]:
write_to

<_io.TextIOWrapper name='recipes_text.txt' mode='w' encoding='UTF-8'>

In [66]:
recipes

[[['Heat oven to 190C/fan 170C/gas 5. Heat 1 tbsp oil and the butter in a frying pan, then add the onion and fry for 5 mins until softened. Cool slightly. Tip the sausagemeat, lemon zest, breadcrumbs, apricots, chestnuts and thyme into a bowl. Add the onion and cranberries, and mix everything together with your hands, adding plenty of pepper and a little salt.',
   'Cut each chicken breast into three fillets lengthwise and season all over with salt and pepper. Heat the remaining oil in the frying pan, and fry the chicken fillets quickly until browned, about 6-8 mins.',
   'Roll out two-thirds of the pastry to line a 20-23cm springform or deep loose-based tart tin. Press in half the sausage mix and spread to level. Then add the chicken pieces in one layer and cover with the rest of the sausage. Press down lightly.',
   'Roll out the remaining pastry. Brush the edges of the pastry with beaten egg and cover with the pastry lid. Pinch the edges to seal, then trim. Brush the top of the pie 

In [69]:
rec

In [72]:
recipes_text

['Heat oven to 190C/fan 170C/gas 5. Heat 1 tbsp oil and the butter in a frying pan, then add the onion and fry for 5 mins until softened. Cool slightly. Tip the sausagemeat, lemon zest, breadcrumbs, apricots, chestnuts and thyme into a bowl. Add the onion and cranberries, and mix everything together with your hands, adding plenty of pepper and a little salt..Cut each chicken breast into three fillets lengthwise and season all over with salt and pepper. Heat the remaining oil in the frying pan, and fry the chicken fillets quickly until browned, about 6-8 mins..Roll out two-thirds of the pastry to line a 20-23cm springform or deep loose-based tart tin. Press in half the sausage mix and spread to level. Then add the chicken pieces in one layer and cover with the rest of the sausage. Press down lightly..Roll out the remaining pastry. Brush the edges of the pastry with beaten egg and cover with the pastry lid. Pinch the edges to seal, then trim. Brush the top of the pie with egg, then roll 